## PSO方法

In [1]:
from inverse_design import inverse_design
import numpy as np
import pandas as pd
import torch
import torch.nn as nn
import matplotlib.pyplot as plt
import optuna
import torch.optim as optim


In [2]:
toy_alloy_data = pd.read_csv("../toy_alloy_data.csv")
X_name = [f'element {i}' for i in range(1,13)]
Y_name = [f'property {i}' for i in range(1,7)]
X = torch.tensor(toy_alloy_data[X_name].values)
Y = torch.tensor(toy_alloy_data[Y_name].values)

In [6]:
from sklearn.ensemble import RandomForestRegressor
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.svm import SVR
from sklearn.tree import DecisionTreeRegressor


CLF = DecisionTreeRegressor()
RFR = RandomForestRegressor()
GBR = GradientBoostingRegressor()

rfr = RFR.fit(pd.DataFrame(X),pd.DataFrame(Y))
#gbr = GBR.fit(pd.DataFrame(X),pd.DataFrame(Y))
#svr = SVR.fit(pd.DataFrame(X),pd.DataFrame(Y))
clf =CLF.fit(pd.DataFrame(X),pd.DataFrame(Y))

In [11]:
from sklearn.metrics import r2_score,mean_squared_error

bounds = [[0, 1],
          [0, 1],
          [0, 1],
          [0, 1],
          [0, 1],
          [0, 1],
          [0, 1],
          [0, 1],
          [0, 1],
          [0, 1],
          [0, 1],
          [0, 1],
          ]
def loss_func(targets, pred):
    # Define your own loss function to target the material properties you want
    return mean_squared_error(pred, targets)

pso_params = {'c1': 1.5, 'c2': 1.5, 'wmin': 0.4, 'wmax': 0.9,
                      'ga_iter_min': 2, 'ga_iter_max': 10, 'iter_gamma': 10,
                      'ga_num_min': 5, 'ga_num_max': 20, 'num_beta': 15,
                      'tourn_size': 3, 'cxpd': 0.9, 'mutpd': 0.05, 'indpd': 0.5, 'eta': 0.5,
                      'pso_iter': 3, 'swarm_size': 10}

inverse_design(targets=np.array([0.1, 0.2, 0.3, 0.4, 0.5, 0.6]).reshape(-1, 1), loss_func=loss_func,
               bounds=bounds, init_guess=None,
               opt_params={**pso_params},
               model_em = [rfr, clf],
               write_dir='./results/inverse_design',
                       )

C:\ProgramData\Anaconda3\lib\site-packages\deap\creator.py:138: RuntimeWarning: A class named 'FitnessMin' has already been created and it will be overwritten. Consider deleting previous creation of that class or rename it.
  warnings.warn("A class named '{0}' has already been created and it "
C:\ProgramData\Anaconda3\lib\site-packages\deap\creator.py:138: RuntimeWarning: A class named 'Particle' has already been created and it will be overwritten. Consider deleting previous creation of that class or rename it.
  warnings.warn("A class named '{0}' has already been created and it "


ValueError: X has 1 features, but RandomForestRegressor is expecting 12 features as input.

## BO方法

In [24]:
from sklearn.ensemble import RandomForestRegressor
from bayes_opt import BayesianOptimization
from sklearn.metrics import r2_score

RFR = RandomForestRegressor()
rfr = RFR.fit(pd.DataFrame(X),pd.DataFrame(Y))

In [54]:
target = np.array([[1,2,3,4,5,6]])

def gen_bo(ele1,ele2,ele3,ele4,ele5,ele6,ele7,ele8,ele9,ele10,ele11,ele12):
    X_gen = np.array([ele1,ele2,ele3,ele4,ele5,ele6,ele7,ele8,ele9,ele10,ele11,ele12]).reshape(-1,12)
    val = r2_score(rfr.predict(X_gen) + 0.001, target)
    return val


In [55]:

re_bo = BayesianOptimization(
        gen_bo,
        {'ele1': (0.001,1),
        'ele2': (0.001,1),
        'ele3': (0.001,1),
        'ele4': (0.001,1),
        'ele5': (0.001,1),
        'ele6': (0.001,1),
        'ele7': (0.001,1),
        'ele8': (0.001,1),
        'ele9': (0.001,1),
        'ele10': (0.001,1),
        'ele11': (0.001,1),
        'ele12': (0.001,1),  
        }
    )


In [ ]:
re_bo.maximize()

## 数据搜索

In [11]:
import numpy as np
import pandas as pd
import torch
import torch.nn as nn
import optuna
import torch.optim as optim
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import r2_score

In [12]:
toy_alloy_data = pd.read_csv("../toy_alloy_data.csv")
X_name = [f'element {i}' for i in range(1,13)]
Y_name = [f'property {i}' for i in range(1,7)]
X = torch.tensor(toy_alloy_data[X_name].values)
Y = torch.tensor(toy_alloy_data[Y_name].values)

In [13]:
RFR = RandomForestRegressor()
rfr = RFR.fit(pd.DataFrame(X),pd.DataFrame(Y))

In [37]:
def softmax(X):
    X_exp = torch.exp(X)
    partition = X_exp.sum(1, keepdim=True)
    return X_exp / partition

def objective(trial):

    ele1,ele2,ele3,ele4,ele5,ele6,ele7,ele8,ele9,ele10,ele11,ele12 =  \
        trial.suggest_float("element1", 0, 1),trial.suggest_float("element2", 0, 1),\
        trial.suggest_float("element3", 0, 1),trial.suggest_float("element4", 0, 1),\
        trial.suggest_float("element5", 0, 1),trial.suggest_float("element6", 0, 1),\
        trial.suggest_float("element7", 0, 1),trial.suggest_float("element8", 0, 1),\
        trial.suggest_float("element9", 0, 1),trial.suggest_float("element10", 0, 1),\
        trial.suggest_float("element11", 0, 1),trial.suggest_float("element12", 0, 1),
    x = torch.tensor([ele1,ele2,ele3,ele4,ele5,ele6,ele7,ele8,ele9,ele10,ele11,ele12]).reshape(-1,12)
    x = softmax(x)
    y = MODEL.predict(x)
    R2 = r2_score(np.array(y).reshape(6,), TARGET)

    #trial.report(R2)
    if trial.should_prune():
        raise optuna.exceptions.TrialPruned()
    return R2

In [38]:
optuna.logging.set_verbosity(optuna.logging.WARNING)

MODEL = rfr
TARGET = [0.1, 0.2, 0.3, 0.4, 0.5, 0.6]

study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=10000
               #, timeout=600
              )

pruned_trials = [t for t in study.trials if t.state == optuna.trial.TrialState.PRUNED]
complete_trials = [t for t in study.trials if t.state == optuna.trial.TrialState.COMPLETE]

print("Study statistics: ")
print("  Number of finished trials: ", len(study.trials))
print("  Number of pruned trials: ", len(pruned_trials))
print("  Number of complete trials: ", len(complete_trials))

print("Best trial:")
trial = study.best_trial

print("  Value: ", trial.value)

print("  Params: ")
for key, value in trial.params.items():
    print("    {}: {}".format(key, value))

[I 2022-05-16 21:33:31,664] A new study created in memory with name: no-name-a4b05717-af1b-4d4c-887c-d92d0e07e873
[I 2022-05-16 21:33:31,679] Trial 0 finished with value: -0.2533158829487705 and parameters: {'element1': 0.28807700621593757, 'element2': 0.5753028254719619, 'element3': 0.649843389678371, 'element4': 0.6812068590963182, 'element5': 0.6395130929909365, 'element6': 0.7553838276310917, 'element7': 0.13277464316503784, 'element8': 0.6987552366466765, 'element9': 0.5256011373380053, 'element10': 0.09518950435855111, 'element11': 0.030179203787087605, 'element12': 0.7228744986708476}. Best is trial 0 with value: -0.2533158829487705.
[I 2022-05-16 21:33:31,690] Trial 1 finished with value: -0.2524162642682308 and parameters: {'element1': 0.3455909910016848, 'element2': 0.006212759304596749, 'element3': 0.29317720794076685, 'element4': 0.5498791510159518, 'element5': 0.7069130082174647, 'element6': 0.14032892610398484, 'element7': 0.38066317992582843, 'element8': 0.43535188766285

Study statistics: 
  Number of finished trials:  10000
  Number of pruned trials:  0
  Number of complete trials:  10000
Best trial:
  Value:  -0.2496286060047872
  Params: 
    element1: 0.00034964750070404227
    element2: 0.11082486751095781
    element3: 0.007663798071946892
    element4: 0.14535333051748062
    element5: 0.3901805360173824
    element6: 0.7000619939476662
    element7: 0.9877106567490418
    element8: 0.8297666726059734
    element9: 0.9992197309990454
    element10: 0.1753129998059971
    element11: 0.005160322886765656
    element12: 0.33929534996556476
